In [ ]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

In [2]:
%cd ~/sr
%pwd

/workspace/sr


'/workspace/sr'

In [3]:
from datasets import load_dataset, load_metric, Audio

common_voice_train = load_dataset("mozilla-foundation/common_voice_8_0", "sr", split="train+validation", use_auth_token=True)
common_voice_test = load_dataset("mozilla-foundation/common_voice_8_0", "sr", split="test", use_auth_token=True)

Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/sr/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)
Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/sr/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)


In [4]:
common_voice_train.cleanup_cache_files()
common_voice_test.cleanup_cache_files()

0

In [5]:
common_voice_train = common_voice_train.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])
common_voice_test = common_voice_test.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])

In [6]:
from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML

def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)
    
    df = pd.DataFrame(dataset[picks])
    display(HTML(df.to_html()))

In [7]:
show_random_elements(common_voice_train.remove_columns(["path", "audio"]), num_examples=10)

In [8]:
import re
chars_to_remove_regex = '[\,\?\.\!\-\;\:\/\"\“\„\%\”\�\–\'\`\«\»\—\’\…\³cejy]'


CHARS = {
    'ü': 'ue',
    'ö': 'oe',
    'ï': 'i',
    'ë': 'e',
    'ã': 'a',
    'à': 'á',
    'ø': 'o',
    'è': 'é',
    'ê': 'é',
    'å': 'ó',
    'î': 'i',
    'ñ': 'ň',
    'ç': 's',
    'þ': 't',
    'ß': 'ss',
    'ę': 'en',
    'ą': 'an',
    'æ': 'ae',
  }

def replace_chars(sentence):
  result = ''
  for ch in sentence:
    new = CHARS[ch] if ch in CHARS else ch
    result += new

  return result


def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, ' ', batch["sentence"]).lower()
    batch["sentence"] = replace_chars(batch['sentence'])
    batch["sentence"] = " ".join([char for char in batch["sentence"].split(" ") if char != ""])
    return batch


In [9]:
show_random_elements(common_voice_train.map(remove_special_characters).remove_columns(["path", "audio"]), num_examples=10)

0ex [00:00, ?ex/s]

In [10]:
common_voice_train = common_voice_train.map(remove_special_characters)
common_voice_test = common_voice_test.map(remove_special_characters)

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/sr/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8/cache-2b2b6581a24f7582.arrow


0ex [00:00, ?ex/s]

In [11]:
show_random_elements(common_voice_train.remove_columns(["path","audio"]))

In [12]:
def extract_all_chars(batch):
  all_text = " ".join(batch["sentence"])
  vocab = list(set(all_text))
  return {"vocab": [vocab], "all_text": [all_text]}

In [13]:
vocab_train = common_voice_train.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_train.column_names)
vocab_test = common_voice_test.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_test.column_names)

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

In [14]:
vocab_list = list(set(vocab_train["vocab"][0]) | set(vocab_test["vocab"][0]))

In [15]:
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}
vocab_dict

{' ': 0,
 'а': 1,
 'б': 2,
 'в': 3,
 'г': 4,
 'д': 5,
 'е': 6,
 'ж': 7,
 'з': 8,
 'и': 9,
 'к': 10,
 'л': 11,
 'м': 12,
 'н': 13,
 'о': 14,
 'п': 15,
 'р': 16,
 'с': 17,
 'т': 18,
 'у': 19,
 'ф': 20,
 'х': 21,
 'ц': 22,
 'ч': 23,
 'ш': 24,
 'ђ': 25,
 'ј': 26,
 'љ': 27,
 'њ': 28,
 'ћ': 29,
 'џ': 30}

In [16]:
vocab_dict["|"] = vocab_dict[" "]
del vocab_dict[" "]

In [17]:
vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
len(vocab_dict)

33

In [18]:
import json
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)

In [19]:
from transformers import Wav2Vec2CTCTokenizer

tokenizer = Wav2Vec2CTCTokenizer.from_pretrained("./", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")

file ./config.json not found
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [20]:
repo_name = "wav2vec2-xls-r-300m-sr-cv8"

In [21]:
from transformers import Wav2Vec2FeatureExtractor

feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)

In [22]:
from transformers import Wav2Vec2Processor

processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [23]:
# save tokenizer to folder
processor.save_pretrained(repo_name)

In [24]:
common_voice_train[0]["path"]

'cv-corpus-8.0-2022-01-19/sr/clips/common_voice_sr_26981130.mp3'

In [25]:
common_voice_train[0]["audio"]

{'path': 'cv-corpus-8.0-2022-01-19/sr/clips/common_voice_sr_26981130.mp3',
 'array': array([ 0.        ,  0.        ,  0.        , ..., -0.00064078,
        -0.00074123, -0.00046641], dtype=float32),
 'sampling_rate': 48000}

In [26]:
common_voice_train = common_voice_train.cast_column("audio", Audio(sampling_rate=16_000))
common_voice_test = common_voice_test.cast_column("audio", Audio(sampling_rate=16_000))

In [27]:
common_voice_train[0]["audio"]

{'path': 'cv-corpus-8.0-2022-01-19/sr/clips/common_voice_sr_26981130.mp3',
 'array': array([ 0.        ,  0.        ,  0.        , ..., -0.00066616,
        -0.0006498 , -0.00069397], dtype=float32),
 'sampling_rate': 16000}

In [28]:
import IPython.display as ipd
import numpy as np
import random

rand_int = random.randint(0, len(common_voice_train)-1)

print(common_voice_train[rand_int]["sentence"])
ipd.Audio(data=common_voice_train[rand_int]["audio"]["array"], autoplay=True, rate=16000)

и била су


In [29]:
rand_int = random.randint(0, len(common_voice_train)-1)

print("Target text:", common_voice_train[rand_int]["sentence"])
print("Input array shape:", common_voice_train[rand_int]["audio"]["array"].shape)
print("Sampling rate:", common_voice_train[rand_int]["audio"]["sampling_rate"])

Target text: овде код мене
Input array shape: (40320,)
Sampling rate: 16000


In [30]:
def prepare_dataset(batch):
    audio = batch["audio"]

    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [31]:
common_voice_train = common_voice_train.map(prepare_dataset, remove_columns=common_voice_train.column_names)
common_voice_test = common_voice_test.map(prepare_dataset, remove_columns=common_voice_test.column_names)

0ex [00:00, ?ex/s]

0ex [00:00, ?ex/s]

In [32]:
#max_input_length_in_sec = 5.0
#common_voice_train = common_voice_train.filter(lambda x: x < max_input_length_in_sec * processor.feature_extractor.sampling_rate, input_columns=["input_length"])

In [33]:
import torch

from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union

@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.Wav2Vec2Processor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
    """

    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lenghts and need
        # different padding methods
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            return_tensors="pt",
        )
        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                return_tensors="pt",
            )

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [34]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [35]:
wer_metric = load_metric("wer")
cer_metric = load_metric("cer")
metrics = [wer_metric, cer_metric]

In [36]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    pred.label_ids[pred.label_ids == -100] = processor.tokenizer.pad_token_id

    pred_str = processor.batch_decode(pred_ids)
    # we do not want to group tokens when computing the metrics
    label_str = processor.batch_decode(pred.label_ids, group_tokens=False)

    wer = wer_metric.compute(predictions=pred_str, references=label_str)
    cer = cer_metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer, "cer": cer}

In [37]:
from transformers import Wav2Vec2ForCTC

model = Wav2Vec2ForCTC.from_pretrained(
    #"comodoro/wav2vec2-xls-r-300m-west-slavic-cv8", 
    "facebook/wav2vec2-xls-r-300m", 
    attention_dropout=0.2,
    hidden_dropout=0.2,
    feat_proj_dropout=0.1,
    mask_time_prob=0.5,
    layerdrop=0.4,
    ctc_loss_reduction="mean", 
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer),
)

Some weights of the model checkpoint at facebook/wav2vec2-xls-r-300m were not used when initializing Wav2Vec2ForCTC: ['project_q.bias', 'project_q.weight', 'project_hid.weight', 'quantizer.codevectors', 'quantizer.weight_proj.bias', 'project_hid.bias', 'quantizer.weight_proj.weight']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-xls-r-300m and are newly initialized: ['lm_head.bias', 'lm_head.weight']
You should probably TRAIN this model on a down-stream task to be able to use it 

In [38]:
model.freeze_feature_extractor()

/workspace/.local/lib/python3.8/site-packages/transformers/models/wav2vec2/modeling_wav2vec2.py:1700: FutureWarning: The method `freeze_feature_extractor` is deprecated and will be removed in Transformers v5.Please use the equivalent `freeze_feature_encoder` method instead.
  warnings.warn(


In [39]:
from transformers import TrainingArguments

training_args = TrainingArguments(
  output_dir=repo_name,
  group_by_length=True,
  per_device_train_batch_size=16,
  gradient_accumulation_steps=1,
  eval_accumulation_steps=1,
  evaluation_strategy="steps",
  num_train_epochs=800,
  gradient_checkpointing=True,
  fp16=True,
  save_steps=1200,
  eval_steps=1200,
  logging_steps=1200,
  learning_rate=1e-4,
  warmup_steps=300,
  save_total_limit=2,
  report_to="tensorboard"
)

In [40]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=common_voice_train,
    eval_dataset=common_voice_test,
    tokenizer=processor.feature_extractor,
)

Using amp half precision backend


In [41]:
trainer.train()

The following columns in the training set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
/workspace/.local/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use thePyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 1278
  Num Epochs = 800
  Instantaneous batch size per device = 16
  Total train batch size (w. parallel, distributed & accumulation) = 16
  Gradient Accumulation steps = 1
  Total optimization steps = 64000


The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 598
  Batch size = 8
Saving model checkpoint to wav2vec2-xls-r-300m-sr-cv8/checkpoint-1200
Configuration saved in wav2vec2-xls-r-300m-sr-cv8/checkpoint-1200/config.json
Model weights saved in wav2vec2-xls-r-300m-sr-cv8/checkpoint-1200/pytorch_model.bin
Configuration saved in wav2vec2-xls-r-300m-sr-cv8/checkpoint-1200/preprocessor_config.json
The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 598
  Batch size = 8
Saving model checkpoint to wav2vec2-xls-r-300m-sr-cv8/checkpoint-2400
Configuration saved in wav2vec2-xls-r-300m-sr-cv8/checkpoint-2400/config.json
Model weights saved in wav2vec2-xls-r-300m-sr-cv8/checkpoint-2400/pytorch_model.bin
Configuration s

TrainOutput(global_step=64000, training_loss=0.5902130200862884, metrics={'train_runtime': 39016.0873, 'train_samples_per_second': 26.205, 'train_steps_per_second': 1.64, 'total_flos': 8.84302567787997e+19, 'train_loss': 0.5902130200862884, 'epoch': 800.0})

In [42]:
#model.push_to_hub(clone_from=https://huggingface.co/comodoro/wav2vec2-xls-r-300m-west-slavic-cv8)

In [43]:
model.save_pretrained('.')

Configuration saved in ./config.json
Model weights saved in ./pytorch_model.bin


In [44]:
trainer.create_model_card()

Dropping the following result as it does not have all the necessary fields:
{'dataset': {'name': 'common_voice', 'type': 'common_voice', 'args': 'sr'}}
